In [ ]:
pip install kfp_tekton==1.5.* --quiet

In [ ]:
import os, subprocess
TOKEN_FILE = "/run/secrets/kubernetes.io/serviceaccount/token" # same as `oc whoami --show-token`
with open(TOKEN_FILE) as f:
  token = f.read().strip()

APPLICATION_NAME = "sample" # change it to match the name of your DSP application
route_host = subprocess.run(f"oc get routes/ds-pipeline-{APPLICATION_NAME} -ojsonpath={{.spec.host}}", check=True, shell=True).stdout
route = f"https://{route_host}"

In [ ]:
import os
import kfp_tekton
from condition import flipcoin_pipeline

In [ ]:
cert="/run/secrets/kubernetes.io/serviceaccount/ca.crt"
ex = None
for i in range(5):
  try:
    print(f'try #{i}')
    client = kfp_tekton.TektonClient(host=route, existing_token=token, ssl_ca_cert=cert)
    print(f'try #{i} succeeded :)')
    break
  except Exception as e:
    import time;time.sleep(5)
    ex = e
else:
  raise Exception('Could not connect to TektonClient the after multiple tries :/') from ex

In [ ]:
from kfp_tekton.compiler import TektonCompiler
TektonCompiler().compile(flipcoin_pipeline, "results/pipeline.yaml")

In [ ]:
client.create_run_from_pipeline_func(pipeline_func=flipcoin_pipeline, arguments={})